In [1]:
import json
from sqlite_utils import Database
from sqlite_graph import generate_adjacency_tables, in_neighborhood_cte, out_neighborhood_cte

In [2]:
with open("10k-mock-issued-mid-size-containers-issuer2-1690831233411.json") as json_file:
    containers = json.load(json_file)

In [3]:
!rm -f test_merits.db

In [4]:
db = Database('test_merits.db')

In [5]:
class EdgeIterator:
    def __init__(self, containers):
        self._containers = containers
        self._index = 0

    def __iter__(self):
        return self

    def __next__(self):
        if self._index < len(self._containers):
            container = self._containers[self._index]
            source = { 
                "vid": container["issuer"]["id"], 
                "attributes": { 
                    "type": container["issuer"]["type"], 
                    "state": container["issuer"]["state"],
                }
            }
            target = {
                "vid": container["recipient"]["id"], 
                "attributes": { 
                    "type": container["recipient"]["type"], 
                    "state": container["recipient"]["state"],
                } 
            }
            edge = { 
                "eid": container["id"], 
                "sid": container["issuer"]["id"], 
                "tid": container["recipient"]["id"], 
                "label": container["name"], 
                "attributes": { field["name"]: field["value"] for field in container["fields"] },
                "state": container["state"]["name"],
                "container": container,
            }
            self._index += 1
            return { 
                "source": source, 
                "edge": edge, 
                "target": target 
            }
        else:
            raise StopIteration

In [6]:
vertices = []
edges = []

for edge in EdgeIterator(containers):
    vertices.append(edge["source"])
    vertices.append(edge["target"])
    edges.append(edge["edge"])

In [7]:
db['vertex'].insert_all(vertices, pk='vid', ignore=True)

<Table vertex (vid, attributes)>

In [8]:
print(db['vertex'].schema)

CREATE TABLE [vertex] (
   [vid] TEXT PRIMARY KEY,
   [attributes] TEXT
)


In [9]:
[ row for row in db['vertex'].rows ]

[{'vid': 'cfe3bb21-9486-468f-9a70-20045adfce21',
  'attributes': '{"type": "organization", "state": "active"}'},
 {'vid': 'd6db9cdf-ef4c-5729-8e39-891f171875e8',
  'attributes': '{"type": "person", "state": "invited"}'},
 {'vid': '0ae4b18c-48b6-5f89-9b1b-7b4e0b5db360',
  'attributes': '{"type": "person", "state": "invited"}'},
 {'vid': 'a631bfec-36ce-5c41-ae7d-84e6b594020d',
  'attributes': '{"type": "person", "state": "invited"}'},
 {'vid': '37408cd8-895c-58a4-89cf-2325345ccb5c',
  'attributes': '{"type": "person", "state": "invited"}'},
 {'vid': 'f4783b34-99a8-5eb0-891a-6f25d822e58d',
  'attributes': '{"type": "person", "state": "invited"}'},
 {'vid': '68560b10-95aa-550c-ae27-660e2740458c',
  'attributes': '{"type": "person", "state": "invited"}'},
 {'vid': '9204c065-dc8e-544c-bd16-e4a403c5508c',
  'attributes': '{"type": "person", "state": "invited"}'},
 {'vid': '50c337fc-583e-5a8a-bed6-773705a60097',
  'attributes': '{"type": "person", "state": "invited"}'},
 {'vid': '36e0ac17-6903

In [10]:
db['edge'].insert_all(edges, pk='eid', ignore=True)

<Table edge (eid, sid, tid, label, attributes, state, container)>

In [11]:
print(db['edge'].schema)

CREATE TABLE [edge] (
   [eid] TEXT PRIMARY KEY,
   [sid] TEXT,
   [tid] TEXT,
   [label] TEXT,
   [attributes] TEXT,
   [state] TEXT,
   [container] TEXT
)


In [12]:
[ row for row in db['edge'].rows ]

[{'eid': '7a029c87-26d1-4f37-bae0-562542cd9443',
  'sid': 'cfe3bb21-9486-468f-9a70-20045adfce21',
  'tid': 'd6db9cdf-ef4c-5729-8e39-891f171875e8',
  'label': 'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'attributes': '{"First Name": "av", "Last Name": "tewri", "Email": "test-eb1c6b37-679e-52cb-aee1-c8c9ac3e347f@nonsafelist.com", "Issuing Org Name": "org-name-12d60678-170a-5ca5-9a1e-c2cbf9308de1", "DOB": "07/31/2023", "Some Text": "gemiw", "Some Number": "5916545993670656", "Some Markdown": "### h1 Heading Dafdespo eluro napub eviilo ilazuzwec dur cionuovu vises tomvere hakupif dubburra wihsad ibacuhati. Sovcapgo rud pibuh zuvizvut nuvtek ugezane cezolipa vuhem regmasfit kindonul nifinero tobis bomiboban. Tazavca ne woggu soimoek urubanen silbi jusute cawkezen zeulabu esout ob vevben bugra mubuf bohgovo."}',
  'state': 'pending',
  'container': '{"id": "7a029c87-26d1-4f37-bae0-562542cd9443", "acceptedAt": null, "active": true, "activenessFailures": null, "authorizedAt": 

In [13]:
db.execute(f'select eid, label, state from edge where label LIKE "TA Template%"').fetchall()

[('7a029c87-26d1-4f37-bae0-562542cd9443',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'pending'),
 ('c35df026-ae27-437f-ae47-8e5ee3c4aac4',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'pending'),
 ('f32cd92b-34b7-4c70-bb3d-4bb97256637a',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'pending'),
 ('7c72370a-aba0-45bc-abad-8805e5cf1513',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'pending'),
 ('43ec2b3a-6710-4495-a611-641a3fc56dfa',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'pending'),
 ('83d4fb1a-d546-45ac-9080-bfb11c2453f0',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'pending'),
 ('734d013a-6a14-44ed-8e38-9830431a862a',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'pending'),
 ('2457f986-2585-4e87-9481-e262a4135988',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'pending'),
 ('bb6509a8-2149-4664-a79e-ac375a4ce945',
  'TA Template name [2

In [14]:
db.execute(f'select json_extract(edge.attributes, "$.First Name") from edge').fetchall()

[('av',),
 ('abuvan',),
 ('fahufok',),
 ('soje',),
 ('cuzut',),
 ('tu',),
 ('virunvo',),
 ('ra',),
 ('vaim',),
 ('ha',),
 ('kacak',),
 ('walifho',),
 ('neh',),
 ('nalru',),
 ('mamok',),
 ('faige',),
 ('cibuw',),
 ('iga',),
 ('loblo',),
 ('puwi',),
 ('ukaob',),
 ('kiw',),
 ('namsozoz',),
 ('raewi',),
 ('develol',),
 ('edlihed',),
 ('woik',),
 ('gez',),
 ('tufwugut',),
 ('vita',),
 ('fioro',),
 ('sohico',),
 ('eboze',),
 ('mulnacop',),
 ('us',),
 ('ecoho',),
 ('jijodopik',),
 ('nulu',),
 ('adfabkan',),
 ('humeb',),
 ('lonnuvwu',),
 ('wuzoj',),
 ('kejade',),
 ('tawju',),
 ('jo',),
 ('jizodru',),
 ('lik',),
 ('jidaliz',),
 ('genit',),
 ('esino',),
 ('hitfu',),
 ('wu',),
 ('lo',),
 ('luso',),
 ('ketlaim',),
 ('ifri',),
 ('ja',),
 ('vev',),
 ('bessas',),
 ('dovupoura',),
 ('somabugaw',),
 ('nenbi',),
 ('sulacjo',),
 ('ophiw',),
 ('wubnafi',),
 ('dejdos',),
 ('lihho',),
 ('bekopsa',),
 ('toahupu',),
 ('iwijep',),
 ('za',),
 ('ewsi',),
 ('tecnated',),
 ('akeviz',),
 ('isuforli',),
 ('puojcuk',

In [15]:
query_3 = (
    f'select eid, label, json_extract(edge.attributes, "$.Email") '
    'from edge where label LIKE "TA Template%" and '
    'json_extract(edge.attributes, "$.First Name") = "virunvo"'
)

In [16]:
db.execute(query_3).fetchall()

[('734d013a-6a14-44ed-8e38-9830431a862a',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'test-fff08e82-f5ea-5896-9c9f-8525e23a77f7@nonsafelist.com')]

In [17]:
query_4 = (
    f'select json_extract(edge.attributes, "$.Email"), '
    'json_extract(edge.attributes, "$.First Name"), '
    'json_extract(edge.attributes, "$.Last Name") '
    'from edge where label LIKE "TA Template%" and '
    'json_extract(edge.attributes, "$.Email") LIKE "test-34%"'
)

In [18]:
db.execute(query_4).fetchall()

[('test-34b21f60-4187-565d-be54-a4ff096d79a6@nonsafelist.com', 'ecoho', 'wok'),
 ('test-34d07f19-7a4c-5001-a5fe-390e4a58aae3@nonsafelist.com',
  'tuw',
  'mogweput'),
 ('test-340f3f3b-a74c-52b8-8b3d-f3dd4b3ff262@nonsafelist.com',
  'bozovhus',
  'tuhuz'),
 ('test-3464c107-c427-5893-bb5a-8114d8fbc68b@nonsafelist.com',
  'cogleguz',
  'dedbi'),
 ('test-34b64d6c-b577-5535-a274-e0baccf36577@nonsafelist.com',
  'vulifzow',
  'gim'),
 ('test-3401fbb7-d698-5aa2-9f36-111406e40689@nonsafelist.com',
  'jurva',
  'aridu'),
 ('test-3474068c-302d-5934-b88c-e03b96c27846@nonsafelist.com',
  'porwivefa',
  'aj'),
 ('test-34aa8c78-cd03-5ffd-ba56-c6bf70f7cbbd@nonsafelist.com',
  'ardunon',
  'zove'),
 ('test-349a01d3-eecf-5a9c-bd04-a181e9448908@nonsafelist.com',
  'jocarnu',
  'kobehe'),
 ('test-34065174-dfbe-507e-aefd-91168e794c45@nonsafelist.com',
  'bazli',
  'neza'),
 ('test-3488ab0c-1d2c-5c03-aa59-f7aebf0e9cbb@nonsafelist.com', 'ufopu', 'ka'),
 ('test-345a1d86-e4fd-5079-976c-9e207729f90b@nonsafelis

In [19]:
generate_adjacency_tables(db)

In [20]:
print(db['outgoing'].schema)

CREATE TABLE [outgoing] (
   [vid] TEXT PRIMARY KEY,
   [label_78] TEXT,
   [edges_78] TEXT
)


In [21]:
[ row for row in db['outgoing'].rows ]

[{'vid': 'cfe3bb21-9486-468f-9a70-20045adfce21',
  'label_78': 'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'edges_78': '[{"eid": "7a029c87-26d1-4f37-bae0-562542cd9443", "tid": "d6db9cdf-ef4c-5729-8e39-891f171875e8"}, {"eid": "c35df026-ae27-437f-ae47-8e5ee3c4aac4", "tid": "0ae4b18c-48b6-5f89-9b1b-7b4e0b5db360"}, {"eid": "f32cd92b-34b7-4c70-bb3d-4bb97256637a", "tid": "a631bfec-36ce-5c41-ae7d-84e6b594020d"}, {"eid": "7c72370a-aba0-45bc-abad-8805e5cf1513", "tid": "37408cd8-895c-58a4-89cf-2325345ccb5c"}, {"eid": "43ec2b3a-6710-4495-a611-641a3fc56dfa", "tid": "f4783b34-99a8-5eb0-891a-6f25d822e58d"}, {"eid": "83d4fb1a-d546-45ac-9080-bfb11c2453f0", "tid": "68560b10-95aa-550c-ae27-660e2740458c"}, {"eid": "734d013a-6a14-44ed-8e38-9830431a862a", "tid": "9204c065-dc8e-544c-bd16-e4a403c5508c"}, {"eid": "2457f986-2585-4e87-9481-e262a4135988", "tid": "50c337fc-583e-5a8a-bed6-773705a60097"}, {"eid": "bb6509a8-2149-4664-a79e-ac375a4ce945", "tid": "36e0ac17-6903-5f9f-b62d-7c891fa8692e"}

In [22]:
print(db['incoming'].schema)

CREATE TABLE [incoming] (
   [vid] TEXT PRIMARY KEY,
   [label_78] TEXT,
   [edges_78] TEXT
)


In [23]:
[ row for row in db['incoming'].rows ]

[{'vid': 'd6db9cdf-ef4c-5729-8e39-891f171875e8',
  'label_78': 'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'edges_78': '[{"eid": "7a029c87-26d1-4f37-bae0-562542cd9443", "sid": "cfe3bb21-9486-468f-9a70-20045adfce21"}]'},
 {'vid': '0ae4b18c-48b6-5f89-9b1b-7b4e0b5db360',
  'label_78': 'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'edges_78': '[{"eid": "c35df026-ae27-437f-ae47-8e5ee3c4aac4", "sid": "cfe3bb21-9486-468f-9a70-20045adfce21"}]'},
 {'vid': 'a631bfec-36ce-5c41-ae7d-84e6b594020d',
  'label_78': 'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'edges_78': '[{"eid": "f32cd92b-34b7-4c70-bb3d-4bb97256637a", "sid": "cfe3bb21-9486-468f-9a70-20045adfce21"}]'},
 {'vid': '37408cd8-895c-58a4-89cf-2325345ccb5c',
  'label_78': 'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'edges_78': '[{"eid": "7c72370a-aba0-45bc-abad-8805e5cf1513", "sid": "cfe3bb21-9486-468f-9a70-20045adfce21"}]'},
 {'vid': 'f4783b34-99a8-5eb0-891a-6f25d822e58d',
  '

In [24]:
out_neighborhood_cte("cfe3bb21-9486-468f-9a70-20045adfce21", "TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]")

'select vid, json_extract(value, "$.eid") as eid, label_78 as label, json_extract(value, "$.tid") as tid from outgoing, json_each(outgoing.edges_78) where vid = "cfe3bb21-9486-468f-9a70-20045adfce21" and label_78 = "TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]"'

In [25]:
[ row for row in db.execute(out_neighborhood_cte("cfe3bb21-9486-468f-9a70-20045adfce21", "TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]")).fetchall() ]

[('cfe3bb21-9486-468f-9a70-20045adfce21',
  '7a029c87-26d1-4f37-bae0-562542cd9443',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'd6db9cdf-ef4c-5729-8e39-891f171875e8'),
 ('cfe3bb21-9486-468f-9a70-20045adfce21',
  'c35df026-ae27-437f-ae47-8e5ee3c4aac4',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  '0ae4b18c-48b6-5f89-9b1b-7b4e0b5db360'),
 ('cfe3bb21-9486-468f-9a70-20045adfce21',
  'f32cd92b-34b7-4c70-bb3d-4bb97256637a',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'a631bfec-36ce-5c41-ae7d-84e6b594020d'),
 ('cfe3bb21-9486-468f-9a70-20045adfce21',
  '7c72370a-aba0-45bc-abad-8805e5cf1513',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  '37408cd8-895c-58a4-89cf-2325345ccb5c'),
 ('cfe3bb21-9486-468f-9a70-20045adfce21',
  '43ec2b3a-6710-4495-a611-641a3fc56dfa',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'f4783b34-99a8-5eb0-891a-6f25d822e58d'),
 ('cfe3bb21-9486-468f-9a70-20045adfce21',
  '83d4fb1a-d546-4

In [26]:
[ row for row in db.execute(in_neighborhood_cte("cfe3bb21-9486-468f-9a70-20045adfce21", "TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]")).fetchall() ]

[]

In [27]:
[ row for row in db.execute(in_neighborhood_cte("d6db9cdf-ef4c-5729-8e39-891f171875e8", "TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]")).fetchall() ]

[('d6db9cdf-ef4c-5729-8e39-891f171875e8',
  '7a029c87-26d1-4f37-bae0-562542cd9443',
  'TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]',
  'cfe3bb21-9486-468f-9a70-20045adfce21')]

In [28]:
db.execute('select count(eid) from edge where label = "TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]" and state = "pending"').fetchone()[0]

9996

In [29]:
db.execute('select count(eid) from edge where label = "TA Template name [23226f5e-25b9-53a0-aa95-a1ac9cc94043]" and not state = "pending"').fetchone()[0]

0

In [30]:
db.execute('select count(eid) from edge').fetchone()[0]

9996